In [1]:
import pyLPM
import pandas as pd
import RBFN
import RBF
import numpy as np
#import ar2gas as gas

In [2]:
walter = pd.read_csv('data/walker.csv')

In [3]:
walter.drop(columns=['Id','U','T'], inplace=True)

In [4]:
walter.head()

X     Y      V
0  11.0   8.0    0.0
1   8.0  30.0    0.0
2   9.0  48.0  224.4
3   8.0  69.0  434.4
4   9.0  90.0  412.1

In [5]:
walter['Z'] = np.zeros(len(walter))

In [6]:
walter.head()

X     Y      V    Z
0  11.0   8.0    0.0  0.0
1   8.0  30.0    0.0  0.0
2   9.0  48.0  224.4  0.0
3   8.0  69.0  434.4  0.0
4   9.0  90.0  412.1  0.0

In [7]:

exhaust = pd.read_csv('data/walker_fivebyfive_exhaust.csv')

In [8]:
exhaust = exhaust.sort_values(by=['YG+ Gravity Center+','XG+ Gravity Center+'])

In [9]:
exhaust.head()

SN+ Sample Number (READONLY)+  XG+ Gravity Center+  YG+ Gravity Center+  \
0                                1                  8.0                  8.0   
58                              59                 13.0                  8.0   
116                            117                 18.0                  8.0   
174                            175                 23.0                  8.0   
232                            233                 28.0                  8.0   

     copy_stat_mean  
0              7.65  
58             9.37  
116           13.77  
174           51.79  
232           72.53

In [10]:
coordinates = walter[['X','Y','Z']]

In [11]:
RBFN.cluster_centers_evaluation(coordinates=coordinates, 
                                max_num_clusters=40)

# Settinng parameters

In [12]:
n_clus = 200

In [13]:
centers = RBFN.cluster_centers(n_clus=n_clus,
                               coordinates=coordinates)

In [14]:
rbf_n = RBFN.RBFN(cluster_centers=centers, 
          sigma=None)

In [15]:
rbf_n.knn_sigma_definition(neighbors_number=5)

In [16]:
#rbf_n.random_bias()

In [17]:
rbf_n.fit(X=coordinates.values, 
          y=walter.V.values)

In [18]:
grid = pyLPM.utils.autogrid(x=walter.X, y=walter.Y, z=walter.Z, sx=5, sy=5, sz=1)

In [19]:
grid

{'ox': 8.0,
 'oy': 8.0,
 'oz': 0.0,
 'sx': 5,
 'sy': 5,
 'sz': 1,
 'nx': 50,
 'ny': 58,
 'nz': 1}

In [20]:
X = pyLPM.utils.add_coord(grid)

In [21]:
predict = rbf_n.predict(X)

In [22]:
pyLPM.plots.pixelplot(
    grid_dic=grid,
    variable=predict,
    categorical=False,
    points=[[x[0] for x in centers[:,0:1]], [y[0] for y in centers[:,1:2]], np.zeros(len(centers))],
    gap=0,
    title='Walker lake RBFN interpolation',
    x_axis='Easting (m)',
    y_axis='Northing (m)',
    colorscale='Jet',
    colorbartitle='',
    figsize=(700, 700),)

In [23]:
pyLPM.plots.pixelplot(
    grid_dic=grid,
    variable=exhaust.copy_stat_mean,
    categorical=False,
    #points=[[x[0] for x in centers[:,0:1]], [y[0] for y in centers[:,1:2]], np.zeros(len(centers))],
    gap=0,
    title='Walker lake RBFN interpolation',
    x_axis='Easting (m)',
    y_axis='Northing (m)',
    colorscale='Jet',
    colorbartitle='',
    figsize=(700, 700),)

In [24]:
pyLPM.plots.scatter2d(x=predict, y=exhaust.copy_stat_mean)

# Traditional RBF

In [77]:
traditional_rbf = RBF.RBF(4.5,1,1,0,0,0)

In [78]:
traditional_rbf.fit(coordinates.values, walter.V.values)

In [79]:
traditional_predictions = traditional_rbf.predict(X)

In [80]:
pyLPM.plots.pixelplot(
    grid_dic=grid,
    variable=traditional_predictions,
    categorical=False,
    #points=[[x[0] for x in centers[:,0:1]], [y[0] for y in centers[:,1:2]], np.zeros(len(centers))],
    gap=0,
    title='Walker lake RBFN interpolation',
    x_axis='Easting (m)',
    y_axis='Northing (m)',
    colorscale='Jet',
    colorbartitle='',
    figsize=(700, 700),)

In [81]:
pyLPM.plots.scatter2d(x=traditional_predictions, y=exhaust.copy_stat_mean)

# tradidional anisotropic

In [82]:
traditional_anis_rbf = RBF.RBF(4.5,1.6,1,160,0,0)

In [83]:
traditional_anis_rbf.fit(coordinates.values, walter.V.values)

In [84]:
traditional_anis_predictions = traditional_anis_rbf.predict(X)

In [87]:
pyLPM.plots.pixelplot(
    grid_dic=grid,
    variable=traditional_anis_predictions,
    categorical=False,
    points=[walter.X, walter.Y, walter.V],
    gap=0,
    title='Walker lake RBFN interpolation',
    x_axis='Easting (m)',
    y_axis='Northing (m)',
    colorscale='Jet',
    colorbartitle='',
    figsize=(700, 700),)

In [86]:
pyLPM.plots.scatter2d(x=traditional_anis_predictions, y=exhaust.copy_stat_mean)

## Anisotropic

In [ ]:
rbf_anis = RBFN.RBFN(cluster_centers=centers, sigma=None, major_med=1.4, major_min=1, azimuth=160,dip=0,rake=0)

In [ ]:
rbf_anis.knn_sigma_definition(neighbors_number=5)

In [ ]:
rbf_anis.fit(X=coordinates.values, 
          y=walter.V.values)

In [ ]:
predict = rbf_anis.predict(X)

In [ ]:
pyLPM.plots.pixelplot(
    grid_dic=grid,
    variable=predict,
    categorical=False,
    #points=[[x[0] for x in centers[:,0:1]], [y[0] for y in centers[:,1:2]], np.zeros(len(centers))],
    gap=0,
    title='Walker lake RBFN interpolation',
    x_axis='Easting (m)',
    y_axis='Northing (m)',
    colorscale='Jet',
    colorbartitle='',
    figsize=(700, 700),)

In [ ]:
pyLPM.plots.scatter2d(x=predict, y=exhaust.copy_stat_mean)

# Train

In [ ]:
X_train, X_test, y_train, y_test = RBFN.train_test_sets_builder(walter, 'X', 'Y', 'Z', 'V')

In [ ]:
rbf_n.train(8000, X_train, X_test, y_train, y_test, learning_rate_w=0.0006)

In [ ]:
predict_train = rbf_n.predict(X)

In [ ]:
pyLPM.plots.pixelplot(
    grid_dic=grid,
    variable=predict_train,
    categorical=False,
    points=[[x[0] for x in centers[:,0:1]], [y[0] for y in centers[:,1:2]], np.zeros(len(centers))],
    gap=0,
    title='Walker lake RBFN interpolation',
    x_axis='Easting (m)',
    y_axis='Northing (m)',
    colorscale='Jet',
    colorbartitle='',
    figsize=(700, 700),)

In [ ]:
pyLPM.plots.scatter2d(x=predict_train, y=exhaust.copy_stat_mean)

In [ ]:
rbf_n.weights = np.random.randn(n_clus+1)

In [ ]:
predict_random_weights = rbf_n.predict(X)

In [ ]:
pyLPM.plots.pixelplot(
    grid_dic=grid,
    variable=predict_random_weights,
    categorical=False,
    points=[[x[0] for x in centers[:,0:1]], [y[0] for y in centers[:,1:2]], np.zeros(len(centers))],
    gap=0,
    title='Walker lake RBFN interpolation',
    x_axis='Easting (m)',
    y_axis='Northing (m)',
    colorscale='Jet',
    colorbartitle='',
    figsize=(700, 700),)

In [ ]:
pyLPM.plots.scatter2d(x=predict_random_weights, y=exhaust.copy_stat_mean)

In [ ]:
rbf_n.train(10000, X_train, X_test, y_train, y_test, learning_rate_w=0.0006)

In [ ]:
predict_trained_weights = rbf_n.predict(X)

In [ ]:
pyLPM.plots.pixelplot(
    grid_dic=grid,
    variable=predict_trained_weights,
    categorical=False,
    points=[[x[0] for x in centers[:,0:1]], [y[0] for y in centers[:,1:2]], np.zeros(len(centers))],
    gap=0,
    title='Walker lake RBFN interpolation',
    x_axis='Easting (m)',
    y_axis='Northing (m)',
    colorscale='Jet',
    colorbartitle='',
    figsize=(700, 700),)

In [ ]:
pyLPM.plots.scatter2d(x=predict_trained_weights, y=exhaust.copy_stat_mean)

# Trainign with NN

In [ ]:
rbf_n.weights = np.random.randn(n_clus+1)

In [ ]:
rbf_n.train(3000, X_train, X_test, y_train, y_test, neighbors_number=3, learning_rate_w=0.0006)

In [ ]:
predict_trained_knn = rbf_n.predict(X)

In [ ]:
pyLPM.plots.pixelplot(
    grid_dic=grid,
    variable=predict_trained_knn,
    categorical=False,
    points=[[x[0] for x in centers[:,0:1]], [y[0] for y in centers[:,1:2]], np.zeros(len(centers))],
    gap=0,
    title='Walker lake RBFN interpolation',
    x_axis='Easting (m)',
    y_axis='Northing (m)',
    colorscale='Jet',
    colorbartitle='',
    figsize=(700, 700),)

In [ ]:
pyLPM.plots.scatter2d(x=predict_trained_knn, y=exhaust.copy_stat_mean)

In [ ]:
rbf_n.weights = np.random.randn(n_clus+1)

In [ ]:
rbf_n.train(3000, X_train, X_test, y_train, y_test, neighbors_number=6, learning_rate_w=0.0006)

In [ ]:
predict_trained_knn_6 = rbf_n.predict(X)

In [ ]:
pyLPM.plots.pixelplot(
    grid_dic=grid,
    variable=predict_trained_knn_6,
    categorical=False,
    points=[[x[0] for x in centers[:,0:1]], [y[0] for y in centers[:,1:2]], np.zeros(len(centers))],
    gap=0,
    title='Walker lake RBFN interpolation',
    x_axis='Easting (m)',
    y_axis='Northing (m)',
    colorscale='Jet',
    colorbartitle='',
    figsize=(700, 700),)

In [ ]:
pyLPM.plots.scatter2d(x=predict_trained_knn_6, y=predict_trained_knn)

In [ ]:
rbf_n.weights = np.random.randn(n_clus+1)

In [ ]:
rbf_n.fit(X=coordinates.values, 
          y=walter.V.values)

In [ ]:
rbf_n.train(6000, X_train, X_test, y_train, y_test, neighbors_number=5, learning_rate_w=0.003)

In [ ]:
predict_trained_knn_from_fit = rbf_n.predict(X)

In [ ]:
pyLPM.plots.pixelplot(
    grid_dic=grid,
    variable=predict_trained_knn_from_fit,
    categorical=False,
    #points=[[x[0] for x in centers[:,0:1]], [y[0] for y in centers[:,1:2]], np.zeros(len(centers))],
    gap=0,
    title='Walker lake RBFN interpolation',
    x_axis='Easting (m)',
    y_axis='Northing (m)',
    colorscale='Jet',
    colorbartitle='',
    figsize=(700, 700),)

In [ ]:
pyLPM.plots.scatter2d(x=predict_trained_knn_from_fit, y=exhaust.copy_stat_mean)

## anis train

In [ ]:
rbf_anis.weights = np.random.randn(n_clus+1)

In [ ]:
rbf_anis.train(6000, X_train, X_test, y_train, y_test, neighbors_number=None, learning_rate_w=0.0003)

In [ ]:
predict_anist = rbf_anis.predict(X)

In [ ]:
pyLPM.plots.pixelplot(
    grid_dic=grid,
    variable=predict_anist,
    categorical=False,
    #points=[[x[0] for x in centers[:,0:1]], [y[0] for y in centers[:,1:2]], np.zeros(len(centers))],
    gap=0,
    title='Walker lake RBFN interpolation',
    x_axis='Easting (m)',
    y_axis='Northing (m)',
    colorscale='Jet',
    colorbartitle='',
    figsize=(700, 700),)

In [ ]:
pyLPM.plots.scatter2d(x=predict_anist, y=exhaust.copy_stat_mean)